In [1]:
import pandas as pd
fn = r'C:\Users\zerot\Desktop\python\busVisSystem\metadata\TBIS_MS_ROUTE_NODE.csv'
df_rn = pd.read_csv(fn, encoding='utf-8-sig')

fn =  r'C:\Users\zerot\Desktop\python\busVisSystem\metadata\TBIS_MS_STTN.csv'
df_s = pd.read_csv(fn, encoding='utf-8-sig')

fn = r'C:\Users\zerot\Desktop\python\busVisSystem\metadata\TBIS_MS_ROUTE.csv'
df_r = pd.read_csv(fn, encoding='utf-8-sig')

In [ ]:
import math

def haversine(lat1, lon1, lat2, lon2):
    R = 6371  # 지구 반지름 (km)
    phi1 = math.radians(lat1)
    phi2 = math.radians(lat2)
    delta_phi = math.radians(lat2 - lat1)
    delta_lambda = math.radians(lon2 - lon1)

    a = math.sin(delta_phi / 2) ** 2 + \
        math.cos(phi1) * math.cos(phi2) * \
        math.sin(delta_lambda / 2) ** 2
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))

    return R * c

# 영등포 타임스퀘어 3번 게이트 위치
lat, lon = 37.5181, 126.9036 

"""
1. 3번 게이트 근처 버스 정류장 찾기
"""
# haversine 함수를 이용해서 영등포 타임스퀘어 3번 게이트와 각 버스 정류소의 거리는 dist 열로 저장
df_s['dist'] = df_s.apply(lambda row: haversine(row['CRDNT_Y'], row['CRDNT_X'], lat, lon), axis=1)
# 0.3 km, 300 m 이내의 버스 정류소를 df_s_near로 저장
df_s_near = df_s[['STTN_ID', 'CRDNT_X', 'CRDNT_Y']][df_s['dist'] <= 0.3]

"""
2. 근처 버스 정류장에 정거하는 모든 버스 (ROUTE_ID) 찾기
"""

df_routeId_near = df_rn['ROUTE_ID'][df_rn['STTN_ID'].isin(df_s_near['STTN_ID'])].unique()
"""
3. 모든 버스가 정거하는 정류장 찾기
"""
stn_list = df_rn['STTN_ID'][df_rn['ROUTE_ID'].isin(df_routeId_near)].tolist()


array([100100281, 100100085, 111000014, 118900001, 229000017, 100100592,
       118900005, 217000013, 100100306, 100100277, 100100102, 115000010,
       100100097, 213000007, 212000003, 100100094, 210000039, 232000029,
       224000029, 208000016, 219000023, 100100275, 100100308, 100100093,
       100100090, 100100078, 117000002, 100100576, 100100521, 100100272,
       100100292, 100100288, 100100307, 100100511, 100100550, 100100305,
       100100033, 100100273, 219000004, 218000010, 116000004, 219000006,
       118900006, 213000011, 100100602, 218000112, 216000021, 212000002,
       100100248, 100100312, 232000017, 210000036, 229000083, 232000116,
       100100400, 229000097, 232000025, 212000001, 232000007, 100100601])

In [ ]:
import folium
m = folium.Map(location=[df_s_near['CRDNT_Y'].mean(),  df_s_near['CRDNT_X'].mean()], 
                tiles='CartoDB dark_matter', # 빨간색이 잘보이게 타일 바꿈
               zoom_start=17)
for idx, row in df_s_near.iterrows():
    folium.CircleMarker(
        location=[row['CRDNT_Y'], row['CRDNT_X']],  # (lat, lon)
        radius=3,  # 반경 크기
        color="red",  # 원의 색상
        fill=True,  # 채우기 여부
        fill_color="red",  # 채우기 색상
        fill_opacity=0.7,  # 채우기 투명도
        popup=f"Calc:({idx})"  # 마커를 클릭했을 때 표시될 텍스트
    ).add_to(m)
m

In [18]:
df_routeId_near

array([100100281, 100100085, 111000014, 118900001, 229000017, 100100592,
       118900005, 217000013, 100100306, 100100277, 100100102, 115000010,
       100100097, 213000007, 212000003, 100100094, 210000039, 232000029,
       224000029, 208000016, 219000023, 100100275, 100100308, 100100093,
       100100090, 100100078, 117000002, 100100576, 100100521, 100100272,
       100100292, 100100288, 100100307, 100100511, 100100550, 100100305,
       100100033, 100100273, 219000004, 218000010, 116000004, 219000006,
       118900006, 213000011, 100100602, 218000112, 216000021, 212000002,
       100100248, 100100312, 232000017, 210000036, 229000083, 232000116,
       100100400, 229000097, 232000025, 212000001, 232000007, 100100601])

In [23]:
import folium

df = pd.DataFrame({'STTN_ID': stn_list})
df_merged = pd.merge(df, df_s, how='left', on='STTN_ID')

m = folium.Map(location=[df_merged['CRDNT_Y'].mean(),  df_merged['CRDNT_X'].mean()], 
               tiles='CartoDB dark_matter', # 빨간색이 잘보이게 타일 바꿈
               zoom_start=10)
for idx, row in df_merged.iterrows():
    folium.CircleMarker(
        location=[row['CRDNT_Y'], row['CRDNT_X']],  # (lat, lon)
        radius=1,  # 반경 크기
        color="red",  # 원의 색상
        fill=True,  # 채우기 여부
        fill_color="red",  # 채우기 색상
        fill_opacity=0.7,  # 채우기 투명도
        popup=f"Calc:({idx})"  # 마커를 클릭했을 때 표시될 텍스트
    ).add_to(m)
m